In [20]:
import pandas as pd
import numpy as np
import json
import os
import re
from bs4 import BeautifulSoup

In [25]:
def extract_sentences(data, segment, isprint):
    """
    parse Json to get unspecified field count
    
    Args:
        data (string): String of properly formatted JSON.

    Returns:
        
    """
    def allindices(string, sub, offset=0):
        listindex = []
        i = string.find(sub, offset)
        while i >= 0:
            listindex.append(i)
            i = string.find(sub, i + 1)
        return listindex
#     print("Segment:", segment)
    soup = BeautifulSoup()
    left_fullstop = -10000
    left_break_tag = -10000
    right_fullstop = 10000
    right_break_tag = 10000

    dictionary_subcategories = {}
    collated_sentences = []
    json_data = json.loads(data)
    for attribute, value in json_data.items():
        print("attribute:", attribute)
        endIndexInSegment = value["endIndexInSegment"]-1
        if isprint:
            print("endIndexInSegment:", endIndexInSegment)
        startIndexInSegment = value["startIndexInSegment"]
        if isprint:
            print("startIndexInSegment:", startIndexInSegment)

        json_value = value["value"]
        if json_value == "Unspecified":
            continue
        else:
            if startIndexInSegment == 0 and endIndexInSegment == len(segment):
                collated_sentences.append(segment[startIndexInSegment:endIndexInSegment-1].strip())
                continue
            if startIndexInSegment == 0:
                left_fullstop = 0
                left_break_tag = 0
            if endIndexInSegment == len(segment):
                right_fullstop = 0
                right_break_tag = 0
            
            
#             print("value: ", value)
            full_stops = allindices(segment, ".")
            break_tags = allindices(segment, "<br>")
            if isprint:
                print("full_stops: ", full_stops)
            if isprint:
                print("break_tags: ", break_tags)
            left_fullstops = [x for x in full_stops if x <= startIndexInSegment]
            right_fullstops = [x for x in full_stops if x >= endIndexInSegment]
            left_break_tags = [x for x in break_tags if x <= startIndexInSegment]
            right_break_tags = [x for x in break_tags if x >= endIndexInSegment]
            
            if len(left_fullstops) > 1: 
                if left_fullstop is not 0:
                    left_fullstop = max(left_fullstops)+1
            else:
                if len(left_fullstops) == 1:
                    if left_fullstop is not 0:
                        left_fullstop = left_fullstops[0]+1
#                 else:
#                     if len(left_fullstops == 0):
#                         left_fullstop = 0
            

            if len(right_fullstops) > 1: 
                if right_fullstops is not 0:
                    right_fullstop = min(right_fullstops)+1
            else:
                if len(right_fullstops) == 1:
                    if right_fullstop is not 0:
                        right_fullstop = right_fullstops[0]+1


                        
            if len(left_break_tags) > 1: 
                if left_break_tag is not 0:
                    left_break_tag = max(left_break_tags)+4
            else:
                if len(left_break_tags) == 1:
                    if left_break_tag is not 0:
                        left_break_tag = left_break_tags[0]+4
#                 else:
#                     if len(left_fullstops == 0):
#                         left_fullstop = 0





            if len(right_break_tags) > 1: 
                if right_break_tag is not 0:
                    right_break_tag = min(right_break_tags)+4
            else:
                if len(right_break_tags) == 1:
                    if right_break_tag is not 0:
                        right_break_tag = right_break_tags[0]+4
#                 else:
#                     if len(left_fullstops == 0):
#                         left_fullstop = 0

            if isprint:
                print("right_fullstop: ", right_fullstop)
            if isprint:
                print("right_break_tag: ", right_break_tag)
            left = max(left_fullstop, left_break_tag)
            right = min(right_fullstop, right_break_tag)
            if isprint:
                print("Collated segment:", segment[left:right].strip())
            sentence = segment[left:right].strip()
            cleantext = BeautifulSoup(sentence, "lxml").text
            collated_sentences.append(cleantext)
            dictionary_subcategories[attribute] = cleantext
    print("dictionary_subcategories: ", dictionary_subcategories)
    return collated_sentences, dictionary_subcategories

In [26]:
def create_df():
    """
    parse Json to get unspecified field count
    
    Args:
        data (string): String of properly formatted JSON.

    Returns:
        
    """
    dictionary = {}
    path_sanitized_policies = "/Users/bhramoss/Documents/CMU/sem2/PDS/pds_project/MineB4USign/OPP-115/sanitized_policies/"
    path_annotations = "/Users/bhramoss/Documents/CMU/sem2/PDS/pds_project/MineB4USign/OPP-115/annotations/"
    regex_html = "(.*).html"
    regex_csv = "(.*).csv"
    for filename_sanitized_policies in os.listdir(path_sanitized_policies):
        if filename_sanitized_policies == ".DS_Store":
            continue
        m = re.match(regex_html, filename_sanitized_policies)
        groups = m.groups()
        filename_sanitized_policies_no_extension = groups[0]
#         print("filename: ", filename_sanitized_policies)
        path_sanitized_policies_file = path_sanitized_policies + "/" + filename_sanitized_policies 
#         file_list = os.listdir(path_annotations)
        f = open(path_sanitized_policies_file, "r")
        content = f.read()
        segments = content.split("|||")
        path_annotations_file = path_annotations + filename_sanitized_policies_no_extension + ".csv"
#         print("path_annotations_file: ", path_annotations_file)
        annotations = pd.read_csv(path_annotations_file, keep_default_na = False, names = ["annotation ID", "batch ID", "annotator ID", "policy ID", "segment ID", "category name", "attribute-value", "policy URL", "date"]) 
        annotations = pd.concat([annotations, pd.get_dummies(annotations['category name'])], axis=1)
#         adding the segments to the dataframe.
        sLength = len(annotations['annotation ID'])
        annotations['segment'] = pd.Series(np.random.randn(sLength), index=annotations.index)
        annotations['segment'] = annotations['segment'].astype('str')
        
        annotations['collated_sentences'] = pd.Series(np.random.randn(sLength), index=annotations.index)
        annotations['collated_sentences'] = annotations['segment'].astype('str')
        annotations['sub_categories_dictionary'] = pd.Series(np.random.randn(sLength), index=annotations.index)

        count = 1
        for i, row in annotations.iterrows():
            segment_id = row['segment ID']
            annotations.at[i, 'segment'] = segments[segment_id]
#             print("annotations.at[i, 'attribute-value']", annotations.at[i, 'attribute-value'])
#             print("segments[segment_id]: ", segments[segment_id])
            count +=1
            istrue = False
            if count == 8:
                istrue = True
            collated_sentences, dictionary_subcategories = extract_sentences(annotations.at[i, 'attribute-value'], segments[segment_id], istrue)
#             if count == 8:
#                 print("segments[segment_id]:", segments[segment_id])
#                 print("collated_sentences: ", collated_sentences)
            annotations.at[i, 'collated_sentences'] = collated_sentences
            annotations.at[i, 'sub_categories_dictionary'] = dictionary_subcategories
            
        dictionary[filename_sanitized_policies_no_extension] = annotations
    return dictionary
        
        
create_df()

/Users/bhramoss/anaconda3/lib/python3.6/site-packages/bs4/__init__.py:181: UserWarning: No parser was explicitly specified, so I'm using the best available HTML parser for this system ("lxml"). This usually isn't a problem, but if you run this code on another system, or in a different virtual environment, it may use a different parser and behave differently.

The code that caused this warning is on line 193 of the file /Users/bhramoss/anaconda3/lib/python3.6/runpy.py. To get rid of this warning, change code that looks like this:

 BeautifulSoup(YOUR_MARKUP})

to this:

 BeautifulSoup(YOUR_MARKUP, "lxml")

  markup_type=markup_type))


attribute: Other Type
dictionary_subcategories:  {'Other Type': 'Privacy Policy   Last Modified: March 25, 2013 '}
attribute: Other Type
dictionary_subcategories:  {'Other Type': 'This is the privacy policy ("Privacy Policy") for LatinPost.com ("Site," "we," "us," or "our"). This Privacy Policy is intended to explain our privacy practices and covers the following areas:     When This Privacy Policy Applies.     U.S. Governing Law; Safe Harbor.     Collection and Use of Personal Information and Other Information (Other than Wireless Marketing Services and Associated Promotional Opportunities).     Opting-out of Certain Uses of your Personal Information and Other Information (Other than Wireless Marketing Services and Associated Promotional Opportunities).     Wireless Marketing Services and Associated Promotional Opportunities.     Sharing and Disclosure of Personal Information and Other Information.     Reviewing, Updating or Deleting Certain Information.     Protection of Information.

attribute: Identifiability
attribute: Does/Does Not
attribute: User Type
attribute: Purpose
dictionary_subcategories:  {'Collection Mode': '  ii.', 'Choice Scope': '  ii.', 'Personal Information Type': "Further, for example, to the extent we offer such services, if you order any of our various Products (as defined in the Terms of Use Agreement), in addition to your name and contact information, we will also collect and may maintain your billing address, shipping address, Product selections, your credit card or other payment instrument information, your order number and information about your computer's internet address and website which may have referred or directed you to the Site (e.", 'Choice Type': '', 'Identifiability': '', 'Does/Does Not': '', 'User Type': '', 'Purpose': "Further, for example, to the extent we offer such services, if you order any of our various Products (as defined in the Terms of Use Agreement), in addition to your name and contact information, we will also col

attribute: Action First-Party
attribute: Personal Information Type
attribute: Choice Type
attribute: Identifiability
attribute: Does/Does Not
attribute: User Type
attribute: Purpose
dictionary_subcategories:  {'Does/Does Not': '  Responding to your questions or other requests;  ', 'Purpose': '  Responding to your questions or other requests;  '}
attribute: Collection Mode
attribute: Choice Scope
attribute: Action First-Party
attribute: Personal Information Type
attribute: Choice Type
attribute: Identifiability
attribute: Does/Does Not
attribute: User Type
attribute: Purpose
dictionary_subcategories:  {'Collection Mode': "  Contacting you regarding your use of the Site, for informational purposes related to the Site or, in our discretion, regarding changes to the Site's policies;  ", 'Choice Scope': "  Contacting you regarding your use of the Site, for informational purposes related to the Site or, in our discretion, regarding changes to the Site's policies;  ", 'Choice Type': "  Contac

attribute: User Type
attribute: Purpose
attribute: Personal Information Type
dictionary_subcategories:  {'Choice Type': 'Standard rate Promotions will be subject to either the "single opt-in" or the "double-opt-in" (Site/SMS) method, at the discretion of Latin Post\'s depending on the type of Promotion.', 'Choice Scope': 'Registration.', 'User Type': "To the extent we provide wireless marketing services, there are two registration methods provided for Latin Post'swireless marketing services.", 'Purpose': "To the extent we provide wireless marketing services, there are two registration methods provided for Latin Post'swireless marketing services."}
attribute: Choice Type
attribute: Choice Scope
attribute: User Type
attribute: Purpose
attribute: Personal Information Type
dictionary_subcategories:  {'Choice Type': 'Standard rate Promotions will be subject to either the "single opt-in" or the "double-opt-in" (Site/SMS) method, at the discretion of Latin Post\'s depending on the type of Pro

...

attribute: User Type
attribute: Purpose
dictionary_subcategories:  {'Action First-Party': 'We use personal information and non-personal information for internal purposes, including: ', 'Personal Information Type': 'We use personal information and non-personal information for internal purposes, including: ', 'Identifiability': 'We use personal information and non-personal information for internal purposes, including: ', 'Does/Does Not': 'We use personal information and non-personal information for internal purposes, including: ', 'Purpose': 'We use personal information and non-personal information for internal purposes, including: '}
attribute: Collection Mode
attribute: Choice Scope
attribute: Action First-Party
attribute: Personal Information Type
attribute: Choice Type
attribute: Identifiability
attribute: Does/Does Not
attribute: User Type
attribute: Purpose
dictionary_subcategories:  {'Collection Mode': '  enhancing your experience at the Site;    performing administration and tech

attribute: Does/Does Not
attribute: User Type
attribute: Purpose
dictionary_subcategories:  {'Collection Mode': 'Our servers may also automatically collect information about you, your online behavior and your computer, mobile or other device.', 'Personal Information Type': ', CPU speed, connection speed, browser type, operating system, device identifier) and geographic location of you and/or your computer, mobile or other device, as well as date/time stamp, IP address, pages visited, time of visits, content viewed, ads viewed, the site(s), application(s), destination(s), and/or service(s) you arrived from, and other clickstream data.', 'Does/Does Not': 'Our servers may also automatically collect information about you, your online behavior and your computer, mobile or other device.'}
attribute: Collection Mode
attribute: Choice Scope
attribute: Action First-Party
attribute: Personal Information Type
attribute: Choice Type
attribute: Identifiability
attribute: Does/Does Not
attribute: Us

attribute: Personal Information Type
attribute: Choice Type
attribute: Identifiability
attribute: Does/Does Not
attribute: User Type
attribute: Purpose
dictionary_subcategories:  {'Collection Mode': 'I.', 'Choice Scope': 'I.', 'Choice Type': 'I.', 'Identifiability': 'We reserve the right to identify you from your Registration Information and/or to merge or co-mingle anonymous or non-personally identifiable data about you, your offline and online behavior, and/or your computer, mobile or other device (including its geographic location), with your Registration Information and/or other personally identifiable data for any lawful business purpose.', 'Does/Does Not': '', 'User Type': ''}
attribute: Other Type
dictionary_subcategories:  {'Other Type': 'A. The Service will at times place and/or store code or other types of information and/or devices (e.g., cookies) on your computer, mobile or other device (Local Device Storage). We may use Local Device Storage for any lawful business purpose,

attribute: Purpose
dictionary_subcategories:  {'Collection Mode': 'G.', 'Choice Scope': 'G.', 'Action First-Party': 'We reserve the right to use, transfer, sell, and share aggregated, anonymous data about our users as a group for any lawful business purpose, such as analyzing usage trends and seeking compatible advertisers, sponsors, clients and customers.', 'Choice Type': '', 'Identifiability': 'We reserve the right to use, transfer, sell, and share aggregated, anonymous data about our users as a group for any lawful business purpose, such as analyzing usage trends and seeking compatible advertisers, sponsors, clients and customers.', 'Does/Does Not': '', 'User Type': '', 'Purpose': 'We reserve the right to use, transfer, sell, and share aggregated, anonymous data about our users as a group for any lawful business purpose, such as analyzing usage trends and seeking compatible advertisers, sponsors, clients and customers.'}
attribute: Third Party Entity
attribute: Choice Scope
attribut

ValueError: Must have equal len keys and value when setting with an iterable

Json extraction for unspecified value done below

In [10]:
def parse_api_response(data, key):
    """
    parse Json to get unspecified field count
    
    Args:
        data (string): String of properly formatted JSON.

    Returns:
        
    """
    dictionary = {}
    unspecified_count = 0
    specified_count = 0
    for row in data:
        json_data = json.loads(row)
        for attribute, value in json_data.items():
            for inner_attribute, inner_value in value.items():
#                 print("inner_attribute--->: ", inner_attribute)
#                 == is working, 'is' is not working why ?
                if inner_attribute == "value" and inner_value == "Unspecified":
                    unspecified_count += 1
                else:
                    if inner_attribute == "value":
                        specified_count += 1
    
    print("unspecified_count: ", unspecified_count)
    print("specified_count: ", specified_count)
    dictionary[key] = float(specified_count/(specified_count+unspecified_count))
    print(dictionary)

parse_api_response(annotations['attribute-value'], 'http://www.theatlantic.com/privacy-policy/')